In [1]:
! nvidia-smi

Sat Mar 30 19:43:44 2024       
+---------------------------------------------------------------------------------------+
| NVIDIA-SMI 545.23.08              Driver Version: 545.23.08    CUDA Version: 12.3     |
|-----------------------------------------+----------------------+----------------------+
| GPU  Name                 Persistence-M | Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp   Perf          Pwr:Usage/Cap |         Memory-Usage | GPU-Util  Compute M. |
|                                         |                      |               MIG M. |
|=========================================+======================+======================|
|   0  NVIDIA A100-SXM4-40GB          Off | 00000000:C1:00.0 Off |                    0 |
| N/A   32C    P0              49W / 400W |      4MiB / 40960MiB |      0%      Default |
|                                         |                      |             Disabled |
+-----------------------------------------+----------------------+--

In [4]:
!pip -q install torch transformers datasets librosa noisereduce accelerate evaluate -U

In [ ]:
!pip install torch==2.2.0
!pip install transformers==4.39.2

Defaulting to user installation because normal site-packages is not writeable
     |█████████████▋                  | 320.8 MB 192.7 MB/s eta 0:00:03

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



     |█████████████████████████████▋  | 700.0 MB 58.8 MB/s eta 0:00:012

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



     |████████████████████████████████| 755.5 MB 28 kB/s s eta 0:00:01
  Attempting uninstall: torch
    Found existing installation: torch 2.2.2
    Uninstalling torch-2.2.2:
      Successfully uninstalled torch-2.2.2


In [3]:
!pip install huggingface-hub

Defaulting to user installation because normal site-packages is not writeable


In [1]:
import warnings
warnings.filterwarnings('ignore')

import pandas as pd
import numpy as np
from datasets import Dataset, load_dataset, load_metric
import soundfile as sf
import random
import librosa
import noisereduce
from IPython.display import Audio, display
import transformers
from transformers import AutoFeatureExtractor, pipeline
from transformers import AutoModelForAudioClassification, Trainer, TrainingArguments, ASTForAudioClassification
import evaluate
from accelerate import Accelerator
import torch 

In [5]:
unique_dataset = pd.read_csv('train_metadata.csv').drop_duplicates(subset=['label'])
label_to_intent_mapping = dict(zip(unique_dataset['label'], unique_dataset['medical intent']))
id2label = dict(sorted(label_to_intent_mapping.items()))
label2id = {v: k for k, v in id2label.items()}

In [6]:
print(label2id)
print('-'*100)
print(id2label)

{'Abdominal Pain and Weakness': 0, 'Dermatological Issues': 1, 'Head and Neck Discomfort': 2, 'Musculoskeletal Pain': 3, 'Respiratory and Ear Issues': 4, 'Wound Trauma': 5}
----------------------------------------------------------------------------------------------------
{0: 'Abdominal Pain and Weakness', 1: 'Dermatological Issues', 2: 'Head and Neck Discomfort', 3: 'Musculoskeletal Pain', 4: 'Respiratory and Ear Issues', 5: 'Wound Trauma'}


#### Creating custom audio datasets

In [37]:
# train_metadata = pd.read_csv('metadata_train.csv').drop(['intent', 'phrase'], axis=1)
# train_metadata.to_csv('recordings/train/metadata.csv', index=False)

In [38]:
# val_metadata = pd.read_csv('metadata_validation.csv').drop(['intent', 'phrase'], axis=1)
# val_metadata.to_csv('recordings/validation/metadata.csv', index=False)

In [39]:
# test_metadata = pd.read_csv('metadata_test.csv').drop(['intent', 'phrase'], axis=1)
# test_metadata.to_csv('recordings/test/metadata.csv', index=False)

In [36]:
# no need to run again since we have pushed this dataset to Huggingface hub
# dataset = load_dataset('audiofolder', data_dir='recordings/') 
# dataset.push_to_hub('shreyas1104/medical-intent-audio-dataset') 

dataset = load_dataset('shreyas1104/medical-intent-audio-dataset-consolidated')

In [37]:
train_dataset = dataset['train']
train_dataset[0]

{'audio': {'path': '1249120_13842059_105045085.wav',
  'array': array([-0.02618408, -0.02441406, -0.01422119, ..., -0.00292969,
          0.00552368, -0.00299072]),
  'sampling_rate': 48000},
 'label': 3}

In [38]:
test_dataset = dataset['test']
test_dataset[0]

{'audio': {'path': '1249120_44142156_100535941.wav',
  'array': array([-0.00067139, -0.0007019 , -0.00064087, ...,  0.00033569,
          0.00027466,  0.00018311]),
  'sampling_rate': 48000},
 'label': 4}

#### Checking a few random examples from train dataset

In [39]:
validation_dataset = dataset['validation']
validation_dataset[0]

{'audio': {'path': '1249120_44246595_101823153.wav',
  'array': array([ 3.35693359e-04,  3.35693359e-04,  2.74658203e-04, ...,
          0.00000000e+00,  0.00000000e+00, -3.05175781e-05]),
  'sampling_rate': 44100},
 'label': 5}

In [40]:
for _ in range(5):
    rand_idx = random.randint(0, len(train_dataset) - 1)
    example = train_dataset[rand_idx]
    audio = example["audio"]

    print(f"Label: {example['label']}")
    print(f"Shape: {audio['array'].shape}, sampling rate: {audio['sampling_rate']}")
    display(Audio(audio["array"], rate=audio["sampling_rate"]))
    print()

Label: 2
Shape: (327680,), sampling rate: 48000



Label: 3
Shape: (479232,), sampling rate: 192000



Label: 1
Shape: (278528,), sampling rate: 48000



Label: 5
Shape: (253952,), sampling rate: 44100



Label: 3
Shape: (253952,), sampling rate: 48000


#### Preprocessing

In [41]:
model_checkpoint = 'kunal18/wav2vec2-conformer-rel-pos-large-medical-intent-medical-intent_v3' #'kunal18/wav2vec2-conformer-rel-pos-large-medical-intent_v3' #'facebook/wav2vec2-conformer-rel-pos-large'
feature_extractor = AutoFeatureExtractor.from_pretrained(model_checkpoint)
feature_extractor

Wav2Vec2FeatureExtractor {
  "do_normalize": true,
  "feature_extractor_type": "Wav2Vec2FeatureExtractor",
  "feature_size": 1,
  "padding_side": "right",
  "padding_value": 0.0,
  "processor_class": "Wav2Vec2Processor",
  "return_attention_mask": true,
  "sampling_rate": 16000
}

In [42]:
max_duration = 10  # seconds

In [43]:
def preprocess_function(examples):
    audio_arrays = [x["array"] for x in examples["audio"]]
    
    # Resample audio to 16 kHz
    resampled_audio = []
    for audio in audio_arrays:
        resampled_audio.append(librosa.resample(audio, orig_sr=48000, target_sr=16000))
    
    # Apply noise reduction
    denoised_audio = []
    for audio in resampled_audio:
        noise_reduced_audio = noisereduce.reduce_noise(y=audio, sr=16000)
        denoised_audio.append(noise_reduced_audio)
    
    # Normalize audio
    normalized_audio = []
    for audio in denoised_audio:
        normalized_audio.append(audio / np.max(np.abs(audio)))
    
    # Apply dynamic range compression (optional)
    compressed_audio = []
    for audio in normalized_audio:
        compressed_audio.append(0.5 * audio / np.max(np.abs(audio)))
    
    inputs = feature_extractor(
        compressed_audio,
        sampling_rate=feature_extractor.sampling_rate,
        max_length=int(feature_extractor.sampling_rate * max_duration),
        truncation=True,
    )
    return inputs

In [44]:
encoded_train = train_dataset.map(preprocess_function, remove_columns=['audio'], batched=True)

In [45]:
encoded_validation = validation_dataset.map(
    preprocess_function, remove_columns=['audio'], batched=True
)

In [46]:
encoded_test = test_dataset.map(
    preprocess_function, remove_columns=['audio'], batched=True
)

#### Training

In [ ]:
# model_checkpoint = 'MIT/ast-finetuned-audioset-10-10-0.4593'

In [ ]:
# feature_extractor = AutoFeatureExtractor.from_pretrained(model_checkpoint)
# feature_extractor

In [47]:
num_labels = len(label2id.keys())

model = AutoModelForAudioClassification.from_pretrained(
    model_checkpoint,
    num_labels=num_labels,
    label2id=label2id,
    id2label=id2label,
)


# model = ASTForAudioClassification.from_pretrained(
#     model_checkpoint,
#     num_labels=num_labels,
#     label2id=label2id,
#     id2label=id2label,
#     ignore_mismatched_sizes=True
# )

In [52]:
model_name = model_checkpoint.split("/")[-1]
model_name = f"{model_name}-medical-intent_v10"

In [53]:
def compute_metrics(eval_pred):
    """Computes accuracy on a batch of predictions"""
    metric1 = load_metric('accuracy')
    metric2 = load_metric('precision')
    metric3 = load_metric('recall')
    predictions = np.argmax(eval_pred.predictions, axis=1)
    labels = eval_pred.label_ids
    accuracy = metric1.compute(predictions=predictions, references=labels)['accuracy']
    precision = metric2.compute(predictions=predictions, references=labels, average='weighted')['precision']
    recall = metric3.compute(predictions=predictions, references=labels, average='weighted')['recall']
    return {'accuracy':accuracy, 'precision':precision, 'recall':recall}

In [32]:
from huggingface_hub import notebook_login

notebook_login()

In [54]:
from huggingface_hub import interpreter_login

interpreter_login()


    _|    _|  _|    _|    _|_|_|    _|_|_|  _|_|_|  _|      _|    _|_|_|      _|_|_|_|    _|_|      _|_|_|  _|_|_|_|
    _|    _|  _|    _|  _|        _|          _|    _|_|    _|  _|            _|        _|    _|  _|        _|
    _|_|_|_|  _|    _|  _|  _|_|  _|  _|_|    _|    _|  _|  _|  _|  _|_|      _|_|_|    _|_|_|_|  _|        _|_|_|
    _|    _|  _|    _|  _|    _|  _|    _|    _|    _|    _|_|  _|    _|      _|        _|    _|  _|        _|
    _|    _|    _|_|      _|_|_|    _|_|_|  _|_|_|  _|      _|    _|_|_|      _|        _|    _|    _|_|_|  _|_|_|_|

    A token is already saved on your machine. Run `huggingface-cli whoami` to get more information or `huggingface-cli logout` if you want to log out.
    Setting a new token will erase the existing one.
    To login, `huggingface_hub` requires a token generated from https://huggingface.co/settings/tokens .


Enter your token (input will not be visible):  ········
Add token as git credential? (Y/n)  n


Token is valid (permission: write).
Your token has been saved to /home/gupta.aditi/.cache/huggingface/token
Login successful


In [55]:
args = TrainingArguments(
    model_name,
    hub_model_id=f"kunal18/{model_name}",
    evaluation_strategy='epoch',
    save_strategy='epoch',
    learning_rate=0.0001,
    per_device_train_batch_size=4,
    gradient_accumulation_steps=16,
    per_device_eval_batch_size=4,
    num_train_epochs=4,
    warmup_ratio=0.1,
    logging_steps=10,
    load_best_model_at_end=True,
    push_to_hub=True,
)

In [56]:
trainer = Trainer(
    model,
    args,
    train_dataset=encoded_train,
    eval_dataset=encoded_validation,
    tokenizer=feature_extractor,
    compute_metrics=compute_metrics,
)

Detected kernel version 3.10.0, which is below the recommended minimum of 5.5.0; this can cause the process to hang. It is recommended to upgrade the kernel to the minimum version or higher.


In [57]:
torch.cuda.empty_cache()

In [ ]:
accelerator = Accelerator()
trainer = accelerator.prepare(trainer)
trainer.train()

Detected kernel version 3.10.0, which is below the recommended minimum of 5.5.0; this can cause the process to hang. It is recommended to upgrade the kernel to the minimum version or higher.
Failed to detect the name of this notebook, you can set it manually with the WANDB_NOTEBOOK_NAME environment variable to enable code saving.
wandb: Logging into wandb.ai. (Learn how to deploy a W&B server locally: https://wandb.me/wandb-server)
wandb: You can find your API key in your browser here: https://wandb.ai/authorize
wandb: Paste an API key from your profile and hit enter, or press ctrl+c to quit:

  ········


wandb: ERROR API key must be 40 characters long, yours was 37
wandb: Logging into wandb.ai. (Learn how to deploy a W&B server locally: https://wandb.me/wandb-server)
wandb: You can find your API key in your browser here: https://wandb.ai/authorize
wandb: Paste an API key from your profile and hit enter, or press ctrl+c to quit:

  ········


wandb: Appending key for api.wandb.ai to your netrc file: /home/gupta.aditi/.netrc


In [ ]:
trainer.evaluate()

In [ ]:
trainer.push_to_hub()

#### Evaluation on Test set

In [ ]:
# finetuned_model = pipeline('audio-classification', model='shreyas1104/wav2vec2-conformer-rel-pos-large-medical-intent-v2')